# Step 1 Install and Load Libraries

In [44]:
# Install libraries if not already installed
#!pip install pandas nltk

# Import necessary libraries
import pandas as pd
import nltk
import re
import math
from collections import defaultdict

# Download NLTK stopwords and punkt tokenizer
#nltk.download("stopwords")
#nltk.download("punkt")

# Initialize stop words and stemmer
stop_words = set(nltk.corpus.stopwords.words("english"))
stemmer = nltk.PorterStemmer()

# Load the CSV dataset
dataset_path = "wiki_movie_plots_deduped.csv"
movies_df = pd.read_csv(dataset_path)

# Display the first few rows to verify the dataset
movies_df.head()


Release Year                             Title Origin/Ethnicity  \
0          1901            Kansas Saloon Smashers         American   
1          1901     Love by the Light of the Moon         American   
2          1901           The Martyred Presidents         American   
3          1901  Terrible Teddy, the Grizzly King         American   
4          1902            Jack and the Beanstalk         American   

                             Director Cast    Genre  \
0                             Unknown  NaN  unknown   
1                             Unknown  NaN  unknown   
2                             Unknown  NaN  unknown   
3                             Unknown  NaN  unknown   
4  George S. Fleming, Edwin S. Porter  NaN  unknown   

                                           Wiki Page  \
0  https://en.wikipedia.org/wiki/Kansas_Saloon_Sm...   
1  https://en.wikipedia.org/wiki/Love_by_the_Ligh...   
2  https://en.wikipedia.org/wiki/The_Martyred_Pre...   
3  https://en.wikipedia.org/wiki/Terrible_Teddy,_...   
4  https://en.wikipedia.org/wiki/Jack_and_the_Bea...   

                                                Plot  
0  A bartender is working at a saloon, serving dr...  
1  The moon, painted with a smiling face hangs ov...  
2  The film, just over a minute long, is composed...  
3  Lasting just 61 seconds and consisting of two ...  
4  The earliest known adaptation of the classic f...

# Step 2 Save document on Json 

In [47]:
# Process all movie titles and plots from the dataset
def get_all_movie_plots(df):
    documents = []
    for _, row in df.iterrows():
        documents.append({
            "title": row['Title'],
            "content": row['Plot']
        })
    return documents

# Fetch all movie plots from the dataset
documents = get_all_movie_plots(movies_df)

# Save the processed documents to a JSON file
with open("all_movie_plots_data.json", "w") as f:
    json.dump(documents, f)

# Display a sample of the documents to verify content
documents[:1]  # Show the first document as an example


[{'title': 'Kansas Saloon Smashers',
  'content': "A bartender is working at a saloon, serving drinks to customers. After he fills a stereotypically Irish man's bucket with beer, Carrie Nation and her followers burst inside. They assault the Irish man, pulling his hat over his eyes and then dumping the beer over his head. The group then begin wrecking the bar, smashing the fixtures, mirrors, and breaking the cash register. The bartender then sprays seltzer water in Nation's face before a group of policemen appear and order everybody to leave.[1]"}]

# Step 3: Processes the documents

In [51]:
# Preprocessing function with text length check and logging
def preprocess_text(text):
    # Check for excessively long text
    max_length = 10000  # Define a reasonable threshold
    if len(text) > max_length:
        text = text[:max_length]  # Truncate if necessary
    
    # Lowercase and remove special characters
    text = text.lower()
    text = re.sub(r"[^a-z0-9\s]", "", text)
    
    # Tokenize, remove stop words, and apply stemming
    tokens = nltk.word_tokenize(text)
    tokens = [stemmer.stem(word) for word in tokens if word not in stop_words]
    return tokens

# Batch processing to avoid large memory usage
processed_documents = []

for i, doc in enumerate(documents):
    try:
        processed_documents.append({
            "title": doc["title"],
            "content": preprocess_text(doc["content"])
        })
        # Print progress for debugging
        if i % 100 == 0:
            print(f"Processed {i}/{len(documents)} documents.")
    except Exception as e:
        print(f"Error processing document {i}: {e}")

# Save processed documents incrementally
with open("processed_data.json", "w") as f:
    json.dump(processed_documents, f)

Processed 0/34886 documents.
Processed 100/34886 documents.
Processed 200/34886 documents.
Processed 300/34886 documents.
Processed 400/34886 documents.
Processed 500/34886 documents.
Processed 600/34886 documents.
Processed 700/34886 documents.
Processed 800/34886 documents.
Processed 900/34886 documents.
Processed 1000/34886 documents.
Processed 1100/34886 documents.
Processed 1200/34886 documents.
Processed 1300/34886 documents.
Processed 1400/34886 documents.
Processed 1500/34886 documents.
Processed 1600/34886 documents.
Processed 1700/34886 documents.
Processed 1800/34886 documents.
Processed 1900/34886 documents.
Processed 2000/34886 documents.
Processed 2100/34886 documents.
Processed 2200/34886 documents.
Processed 2300/34886 documents.
Processed 2400/34886 documents.
Processed 2500/34886 documents.
Processed 2600/34886 documents.
Processed 2700/34886 documents.
Processed 2800/34886 documents.
Processed 2900/34886 documents.
Processed 3000/34886 documents.
Processed 3100/34886

# Step 4: Create inverted index

In [53]:
# Initialize an empty inverted index
inverted_index = defaultdict(dict)

# Populate the inverted index with term frequencies
for doc_id, doc in enumerate(processed_documents):
    for term in doc["content"]:
        if doc_id in inverted_index[term]:
            inverted_index[term][doc_id] += 1
        else:
            inverted_index[term][doc_id] = 1

# Save the inverted index to a JSON file
with open("inverted_index.json", "w") as f:
    json.dump(inverted_index, f)

# Display a small part of the inverted index to verify content
dict(list(inverted_index.items())[:5])  # Show the first 5 terms in the index


{'bartend': {0: 2,
  192: 1,
  231: 4,
  522: 1,
  1047: 2,
  1357: 1,
  1371: 1,
  1772: 1,
  2159: 1,
  2178: 1,
  2468: 1,
  2522: 1,
  2685: 3,
  2820: 1,
  2953: 1,
  3009: 1,
  3331: 1,
  3428: 1,
  3891: 2,
  4064: 1,
  4134: 1,
  4555: 1,
  4624: 1,
  4642: 1,
  5026: 1,
  5229: 2,
  5433: 1,
  5737: 1,
  5792: 1,
  6380: 2,
  6583: 1,
  6603: 1,
  6642: 1,
  6767: 1,
  6797: 1,
  6884: 1,
  7069: 1,
  7166: 1,
  7184: 1,
  7231: 1,
  7271: 1,
  7667: 1,
  7759: 1,
  8140: 3,
  8307: 1,
  8371: 2,
  8766: 4,
  8775: 1,
  8790: 1,
  8858: 1,
  8928: 1,
  9060: 1,
  9142: 1,
  9201: 1,
  9298: 4,
  9492: 1,
  9556: 1,
  9769: 1,
  9875: 1,
  9916: 1,
  9951: 2,
  10180: 1,
  10192: 1,
  10447: 1,
  10569: 1,
  10656: 2,
  10678: 2,
  10813: 1,
  10859: 1,
  10924: 4,
  11122: 1,
  11280: 1,
  11350: 1,
  11477: 2,
  11614: 1,
  11652: 1,
  11662: 1,
  11717: 1,
  11760: 1,
  11781: 1,
  11870: 1,
  11887: 2,
  12025: 1,
  12151: 1,
  12290: 1,
  12319: 1,
  12381: 1,
  12812: 1,


# Step 5:Boolean Retrieval

In [56]:
# Parse the query with Boolean operators
def parse_query(query):
    terms = query.lower().split()
    tokens = []
    operators = {"and", "or", "not"}
    
    for term in terms:
        if term in operators:
            tokens.append(term)
        else:
            processed_term = stemmer.stem(term) if term not in stop_words else ""
            if processed_term:
                tokens.append(processed_term)
    
    return tokens

# Boolean retrieval function
def boolean_retrieval(query_tokens):
    result_set = set(range(len(processed_documents)))  # Start with all documents
    current_operation = "and"
    
    for token in query_tokens:
        if token in {"and", "or", "not"}:
            current_operation = token
        else:
            matching_docs = set(inverted_index.get(token, {}).keys())
            if current_operation == "and":
                result_set &= matching_docs
            elif current_operation == "or":
                result_set |= matching_docs
            elif current_operation == "not":
                result_set -= matching_docs
    
    return list(result_set)

# Step 6:TF-IDF Ranking

In [59]:
# Compute TF-IDF weight for a term in a document
def compute_tf_idf(term, doc_id):
    term_frequency = inverted_index[term].get(doc_id, 0)
    if term_frequency == 0:
        return 0
    document_frequency = len(inverted_index[term])
    inverse_document_frequency = math.log(len(processed_documents) / (1 + document_frequency))
    return term_frequency * inverse_document_frequency

# Rank results by TF-IDF scores
def rank_results_tf_idf(query_tokens, result_docs):
    doc_scores = {}
    for doc_id in result_docs:
        score = 0
        for term in query_tokens:
            if term not in {"and", "or", "not"}:
                score += compute_tf_idf(term, doc_id)
        doc_scores[doc_id] = score
    return sorted(doc_scores.items(), key=lambda x: x[1], reverse=True)


# Step 7:BM25 Ranking

In [62]:
def bm25_score(query_tokens):
    k1 = 1.5  # BM25 constant
    b = 0.75  # BM25 constant
    avg_doc_length = sum(len(doc['content']) for doc in processed_documents) / len(processed_documents)
    
    scores = []
    for doc_id, doc in enumerate(processed_documents):
        doc_length = len(doc["content"])
        score = 0
        
        for term in query_tokens:
            if term not in {"and", "or", "not"}:
                # Term frequency
                tf = doc["content"].count(term)
                
                # Document frequency
                df = len(inverted_index.get(term, []))
                
                # IDF with smoothing
                idf = math.log((len(processed_documents) - df + 0.5) / (df + 0.5) + 1)
                
                # BM25 formula
                term_score = idf * ((tf * (k1 + 1)) / (tf + k1 * (1 - b + b * (doc_length / avg_doc_length))))
                score += term_score
        
        scores.append((doc_id, score))
    
    return sorted(scores, key=lambda x: x[1], reverse=True)

# Step 8: Search Function

In [65]:
def search_documents(query, algorithm="boolean"):
    query_tokens = parse_query(query)

    if algorithm == "boolean":
        # Boolean Retrieval: Display document titles
        results = boolean_retrieval(query_tokens)
        print("\nBoolean Retrieval Results:")
        for doc_id in results:
            print(f"Document: {documents[doc_id]['title']}")
        return results

    elif algorithm == "tf-idf":
        # TF-IDF Ranking: Display document titles and scores
        result_docs = boolean_retrieval(query_tokens)
        ranked_results = rank_results_tf_idf(query_tokens, result_docs)
        print("\nTF-IDF Ranked Results:")
        for doc_id, score in ranked_results:
            print(f"Document: {documents[doc_id]['title']} - Score: {score:.4f}")
        return ranked_results
    
    elif algorithm == "bm25":
        # BM25 Ranking: Display document titles and BM25 scores
        ranked_results = bm25_score(query_tokens)
        print("\nOkapi BM25 Ranked Results:")
        for doc_id, score in ranked_results:  # Use `score` instead of `bm25_score`
            print(f"Document: {documents[doc_id]['title']} - BM25 Score: {score:.4f}")
        return ranked_results

    else:
        print("Unsupported algorithm selected.")
        return []


# Step 9: Interactive Query Loop

In [68]:
def main():
    while True:
        print("\n--- Document Retrieval System ---")
        print("Choose an algorithm:")
        print("1. Boolean Retrieval")
        print("2. TF-IDF")
        print("3. Okapi BM25")
        print("0. Exit")

        choice = input("Enter your choice (0 to exit): ").strip()

        if choice == "0":
            print("Exiting")
            break

        query = input("Enter your search query: ").strip()

        if not query:
            print("Query cannot be empty. Please try again.")
            continue

        if choice == "1":
            print("\nYou selected: Boolean Retrieval")
            search_documents(query, "boolean")
        elif choice == "2":
            print("\nYou selected: TF-IDF Ranking")
            search_documents(query, "tf-idf")
        elif choice == "3":
            print("\nYou selected: Okapi BM25")
            search_documents(query, "bm25")
        else:
            print("Invalid choice. Please enter a number between 0 and 3.")

if __name__ == "__main__":
    main()


--- Document Retrieval System ---
Choose an algorithm:
1. Boolean Retrieval
2. TF-IDF
3. Okapi BM25
0. Exit


Enter your choice (0 to exit):  2
Enter your search query:  fuck



You selected: TF-IDF Ranking

TF-IDF Ranked Results:
Document: S.F.W. - Score: 12.6334
Document: Stone - Score: 12.6334
Document: Happiness - Score: 12.6334
Document: Why Don't You Play in Hell? - Score: 12.6334
Document: The Deer Hunter - Score: 12.6334
Document: Blue Velvet - Score: 6.3167
Document: The People vs. Larry Flynt - Score: 6.3167
Document: Go Goa Gone - Score: 6.3167
Document: Tetsuo: The Iron Man - Score: 6.3167
Document: The Big Lebowski - Score: 6.3167
Document:  Jailbait - Score: 6.3167
Document: Albatross - Score: 6.3167
Document: The Fluffer - Score: 6.3167
Document: The Boy Next Door - Score: 6.3167
Document: 21 Jump Street - Score: 6.3167
Document: Eyes Wide Shut - Score: 6.3167
Document: F.T.W. - Score: 6.3167
Document: Friends with Benefits - Score: 6.3167
Document: The Front - Score: 6.3167
Document: Bulworth - Score: 6.3167
Document: Fifty Shades Darker - Score: 6.3167
Document: Skin & Bone - Score: 6.3167
Document: Fist Fight - Score: 6.3167
Document: Dickie

Enter your choice (0 to exit):  1
Enter your search query:  Movie



You selected: Boolean Retrieval

Boolean Retrieval Results:
Document: Keshava
Document: Andhhagadu
Document: The Dirty Dozen
Document: Divorce American Style
Document: Dosti
Document: Goutham Nanda
Document: Easy Come, Easy Go
Document: Woh Kaun Thi
Document: Enter Laughing
Document: Nene Raju Nene Mantri
Document: The Vow
Document: Anando Brahma
Document: Dosti
Document: Raju Gari Gadhi 2
Document: The Gnome-Mobile
Document: Oxygen
Document: 12 Rounds 2: Reloaded
Document: Grand Slam
Document: Jay. K
Document: 3 Geezers!
Document: Woh Kaun Thi?
Document: The Honey Pot
Document: Guide
Document: Jab Jab Phool Khile
Document: Rishte Naate
Document: Beautiful Creatures
Document: Dus Lakh
Document: Blue Caprice
Document: A Film Johnnie
Document: Torture Garden
Document: Getting Acquainted
Document: The H-Man
Document: Upkar
Document: Farz
Document: Wait Until Dark
Document: Hamraaz
Document: Milan
Document: An Evening in Paris
Document: Welcome to Hard Times
Document: Cheech & Chong's Ani

...


You selected: TF-IDF Ranking

TF-IDF Ranked Results:

--- Document Retrieval System ---
Choose an algorithm:
1. Boolean Retrieval
2. TF-IDF
3. Okapi BM25
0. Exit


Enter your choice (0 to exit):  1
Enter your search query:  fuck AND bro



You selected: Boolean Retrieval

Boolean Retrieval Results:

--- Document Retrieval System ---
Choose an algorithm:
1. Boolean Retrieval
2. TF-IDF
3. Okapi BM25
0. Exit


Enter your choice (0 to exit):  0


Exiting
